-sandbox
<h1>Delta Lake機能プライマー</h1>
<table>
  <tr><th>作者(Mod)</th><th>Masahiko Kitamura</th></tr>
  <tr><th>作者(Original)</th><th>Jixin Jia (Gin)</th></tr>
  <tr><td>期日</td><td>2021/10/15</td></tr>
  <tr><td>バージョン</td><td>2.0</td></tr>
</table>
<img style="margin-top:25px;" src="https://jixjiadatabricks.blob.core.windows.net/images/databricks-logo-small-new.png" width="140">
<hr>
<h3>データレイクに<span style="color='#38a'">信頼性</span>と<span style="color='#38a'">パフォーマンス</span>をもたらす</h3>
<p>本編はローン審査データを使用してDelta LakeでETLを行いながら、その主要機能に関して説明していきます。</p>
<div style="float:left; padding-right:60px; margin-top:20px; margin-bottom:200px;">
  <img src="https://jixjiadatabricks.blob.core.windows.net/images/delta-lake-square-black.jpg" width="220">
</div>

<div style="float:left; margin-top:0px; padding:0;">
  <h3>信頼性</h3>
  <br>
  <ul style="padding-left: 30px;">
    <li>次世代データフォーマット技術</li>
    <li>トランザクションログによるACIDコンプライアンス</li>
    <li>DMLサポート（更新、削除、マージ）</li>
    <li>データ品質管理　(スキーマージ・エンフォース)</li>
    <li>バッチ処理とストリーム処理の統合</li>
    <li>タイムトラベル (データのバージョン管理)</li>
   </ul>

  <h3>パフォーマンス</h3>
  <br>
  <ul style="padding-left: 30px;">
     <li>スケーラブルなメタデータ</li>
    <li>コンパクション (Bin-Packing)</li>
    <li>データ・インデックシング</li>
    <li>データ・スキッピング</li>
    <li>ZOrderクラスタリング</li>
    <li>ストリーム処理による低いレイテンシー</li>
  </ul>
</div>

<div style="display:block; clear:both; padding-top:20px;">
  <div style="background: #ff9; margin-top:10px;">
  <img src="https://jixjiadatabricks.blob.core.windows.net/images/exclamation-yellow.png" width="25px"><span style="padding-left:10px; padding-right:15px;">注) セル12、14と42は意図的にエラーを起こすよう作成しています</span>
</div>
</div>

In [0]:
import re

# Username を取得。
username_raw = dbutils.notebook.entry_point.getDbutils().notebook().getContext().tags().apply('user')
# Username の英数字以外を除去し、全て小文字化。Usernameをファイルパスやデータベース名の一部で使用可能にするため。
username = re.sub('[^A-Za-z0-9]+', '_', username_raw).lower()
dbname = f'delta_db_{username}'

print(f'>>> username => {username}')
print(f'>>> dbname => {dbname}')

>>> username => masahiko_kitamura_databricks_com
>>> dbname => delta_db_masahiko_kitamura_databricks_com

##0. (参考)これまでのデータレイク

In [0]:
%fs head /databricks-datasets/Rdatasets/data-001/csv/ggplot2/diamonds.csv

In [0]:
df = (
  spark.read.format('csv')
  .option('Header', True)
  .option('inferSchema', True)
  .load('/databricks-datasets/Rdatasets/data-001/csv/ggplot2/diamonds.csv') 
)

display(df)

_c0 carat cut color clarity depth table price x y z 1 0.23 Ideal E SI2 61.5 55.0 326 3.95 3.98 2.43 2 0.21 Premium E SI1 59.8 61.0 326 3.89 3.84 2.31 3 0.23 Good E VS1 56.9 65.0 327 4.05 4.07 2.31 4 0.29 Premium I VS2 62.4 58.0 334 4.2 4.23 2.63 5 0.31 Good J SI2 63.3 58.0 335 4.34 4.35 2.75 6 0.24 Very Good J VVS2 62.8 57.0 336 3.94 3.96 2.48 7 0.24 Very Good I VVS1 62.3 57.0 336 3.95 3.98 2.47 8 0.26 Very Good H SI1 61.9 55.0 337 4.07 4.11 2.53 9 0.22 Fair E VS2 65.1 61.0 337 3.87 3.78 2.49 10 0.23 Very Good H VS1 59.4 61.0 338 4.0 4.05 2.39 11 0.3 Good J SI1 64.0 55.0 339 4.25 4.28 2.73 12 0.23 Ideal J VS1 62.8 56.0 340 3.93 3.9 2.46 13 0.22 Premium F SI1 60.4 61.0 342 3.88 3.84 2.33 14 0.31 Ideal J SI2 62.2 54.0 344 4.35 4.37 2.71 15 0.2 Premium E SI2 60.2 62.0 345 3.79 3.75 2.27 16 0.32 Premium E I1 60.9 58.0 345 4.38 4.42 2.68 17 0.3 Ideal I SI2 62.0 54.0 348 4.31 4.34 2.68 18 0.3 Good J SI1 63.4 54.0 351 4.23 4.29 2.7 19 0.3 Good J SI1 63.8 56.0 351 4.23 4.26 2.71 20 0.3 Very Good J SI1 62.7 59.0 351 4.21 4.27 2.66 21 0.3 Good I SI2 63.3 56.0 351 4.26 4.3 2.71 22 0.23 Very Good E VS2 63.8 55.0 352 3.85 3.92 2.48 23 0.23 Very Good H VS1 61.0 57.0 353 3.94 3.96 2.41 24 0.31 Very Good J SI1 59.4 62.0 353 4.39 4.43 2.62 25 0.31 Very Good J SI1 58.1 62.0 353 4.44 4.47 2.59 26 0.23 Very Good G VVS2 60.4 58.0 354 3.97 4.01 2.41 27 0.24 Premium I VS1 62.5 57.0 355 3.97 3.94 2.47 28 0.3 Very Good J VS2 62.2 57.0 357 4.28 4.3 2.67 29 0.23 Very Good D VS2 60.5 61.0 357 3.96 3.97 2.4 30 0.23 Very Good F VS1 60.9 57.0 357 3.96 3.99 2.42 31 0.23 Very Good F VS1 60.0 57.0 402 4.0 4.03 2.41 32 0.23 Very Good F VS1 59.8 57.0 402 4.04 4.06 2.42 33 0.23 Very Good E VS1 60.7 59.0 402 3.97 4.01 2.42 34 0.23 Very Good E VS1 59.5 58.0 402 4.01 4.06 2.4 35 0.23 Very Good D VS1 61.9 58.0 402 3.92 3.96 2.44 36 0.23 Good F VS1 58.2 59.0 402 4.06 4.08 2.37 37 0.23 Good E VS1 64.1 59.0 402 3.83 3.85 2.46 38 0.31 Good H SI1 64.0 54.0 402 4.29 4.31 2.75 39 0.26 Very Good D VS2 60.8 59.0 403 4.13 4.16 2.52 40 0.33 Ideal I SI2 61.8 55.0 403 4.49 4.51 2.78 41 0.33 Ideal I SI2 61.2 56.0 403 4.49 4.5 2.75 42 0.33 Ideal J SI1 61.1 56.0 403 4.49 4.55 2.76 43 0.26 Good D VS2 65.2 56.0 403 3.99 4.02 2.61 44 0.26 Good D VS1 58.4 63.0 403 4.19 4.24 2.46 45 0.32 Good H SI2 63.1 56.0 403 4.34 4.37 2.75 46 0.29 Premium F SI1 62.4 58.0 403 4.24 4.26 2.65 47 0.32 Very Good H SI2 61.8 55.0 403 4.35 4.42 2.71 48 0.32 Good H SI2 63.8 56.0 403 4.36 4.38 2.79 49 0.25 Very Good E VS2 63.3 60.0 404 4.0 4.03 2.54 50 0.29 Very Good H SI2 60.7 60.0 404 4.33 4.37 2.64 51 0.24 Very Good F SI1 60.9 61.0 404 4.02 4.03 2.45 52 0.23 Ideal G VS1 61.9 54.0 404 3.93 3.95 2.44 53 0.32 Ideal I SI1 60.9 55.0 404 4.45 4.48 2.72 54 0.22 Premium E VS2 61.6 58.0 404 3.93 3.89 2.41 55 0.22 Premium D VS2 59.3 62.0 404 3.91 3.88 2.31 56 0.3 Ideal I SI2 61.0 59.0 405 4.3 4.33 2.63 57 0.3 Premium J SI2 59.3 61.0 405 4.43 4.38 2.61 58 0.3 Very Good I SI1 62.6 57.0 405 4.25 4.28 2.67 59 0.3 Very Good I SI1 63.0 57.0 405 4.28 4.32 2.71 60 0.3 Good I SI1 63.2 55.0 405 4.25 4.29 2.7 61 0.35 Ideal I VS1 60.9 57.0 552 4.54 4.59 2.78 62 0.3 Premium D SI1 62.6 59.0 552 4.23 4.27 2.66 63 0.3 Ideal D SI1 62.5 57.0 552 4.29 4.32 2.69 64 0.3 Ideal D SI1 62.1 56.0 552 4.3 4.33 2.68 65 0.42 Premium I SI2 61.5 59.0 552 4.78 4.84 2.96 66 0.28 Ideal G VVS2 61.4 56.0 553 4.19 4.22 2.58 67 0.32 Ideal I VVS1 62.0 55.3 553 4.39 4.42 2.73 68 0.31 Very Good G SI1 63.3 57.0 553 4.33 4.3 2.73 69 0.31 Premium G SI1 61.8 58.0 553 4.35 4.32 2.68 70 0.24 Premium E VVS1 60.7 58.0 553 4.01 4.03 2.44 71 0.24 Very Good D VVS1 61.5 60.0 553 3.97 4.0 2.45 72 0.3 Very Good H SI1 63.1 56.0 554 4.29 4.27 2.7 73 0.3 Premium H SI1 62.9 59.0 554 4.28 4.24 2.68 74 0.3 Premium H SI1 62.5 57.0 554 4.29 4.25 2.67 75 0.3 Good H SI1 63.7 57.0 554 4.28 4.26 2.72 76 0.26 Very Good F VVS2 59.2 60.0 554 4.19 4.22 2.49 77 0.26 Very Good E VVS2 59.9 58.0 554 4.15 4.23 2.51 78 0.26 Very Good D VVS2 62.4 54.0 554 4.08 4.13 2.56 79 0.26 Very Good D VVS

In [0]:
df_cleaned = (
  df
  .where('price between 2000 and 2500') # カラムの条件
  .withColumn('magic_number', df.x * df.y + df.z ) # カラムの追加
  .select('carat', 'cut', 'color', 'clarity', 'price', 'magic_number') # カラムの抽出
)

display( df_cleaned )

carat cut color clarity price magic_number 0.59 Very Good F SI1 2000 32.3 0.7 Ideal J VS1 2000 35.4724 0.7 Good E SI1 2000 33.7896 0.7 Fair E SI1 2000 36.352399999999996 0.58 Very Good F VS1 2001 31.9116 0.77 Very Good J SI2 2001 38.8536 0.77 Very Good J SI2 2001 38.1144 0.72 Very Good G SI2 2001 35.9857 0.73 Very Good H SI1 2001 37.065999999999995 0.55 Ideal E VS1 2001 31.224000000000004 0.55 Ideal E VS1 2001 30.8748 0.53 Ideal G VVS1 2001 30.1778 0.75 Ideal J VS2 2001 38.253 0.71 Ideal J SI1 2001 36.4944 0.57 Premium D SI1 2001 32.196000000000005 0.61 Ideal F VS2 2002 32.929 0.71 Fair E SI2 2002 34.631299999999996 0.74 Premium E SI2 2002 36.9983 0.5 Very Good F VVS2 2003 29.2208 0.5 Very Good E VVS2 2003 29.007700000000003 0.74 Very Good J VS2 2003 37.4115 0.71 Very Good I SI2 2003 36.8404 0.54 Very Good D VS1 2004 30.1042 0.56 Ideal G VVS2 2004 31.7955 0.54 Ideal D VS1 2004 30.3218 0.51 Ideal G VVS1 2005 29.3112 0.51 Very Good G VVS1 2005 30.766 0.51 Ideal G VVS1 2005 29.403999999999996 0.53 Ideal G VVS1 2005 30.532799999999998 0.53 Ideal G VVS1 2005 30.146 0.53 Ideal G VVS1 2005 30.333700000000004 0.7 Premium J VS1 2005 35.9018 0.77 Premium J VS1 2005 37.677 0.77 Fair J VS1 2005 38.1136 0.77 Good E SI2 2005 37.416799999999995 0.71 Ideal H SI1 2006 37.0437 0.72 Ideal J VS1 2006 36.365399999999994 0.71 Premium H SI1 2006 36.5721 0.58 Ideal H VVS1 2006 32.146499999999996 0.76 Very Good D SI2 2006 37.9844 0.67 Very Good D SI1 2007 35.2648 0.71 Good I VS1 2007 34.8934 0.54 Ideal G VVS1 2007 30.665 0.57 Very Good E VS1 2008 33.095 0.71 Very Good I SI1 2008 35.832 0.5 Good E VVS1 2008 30.016800000000003 0.65 Very Good G VS2 2009 33.7838 0.54 Premium D VS2 2009 30.716699999999996 0.62 Premium F VS2 2009 32.8094 0.56 Very Good G VVS2 2010 31.2332 0.56 Very Good G VVS2 2010 31.359899999999996 0.6 Very Good D VS2 2010 32.0324 0.7 Good I VS2 2010 38.367000000000004 0.56 Ideal E VS1 2010 31.4986 0.7 Good I VS2 2010 34.6863 0.7 Very Good G SI1 2010 36.300000000000004 0.56 Ideal E VS1 2010 31.422400000000003 0.7 Premium G SI1 2010 36.2944 0.56 Ideal E VS1 2010 31.422400000000003 0.7 Premium H VS2 2010 35.6488 0.67 Ideal G VS2 2010 34.858399999999996 0.52 Ideal D VS1 2010 30.376 0.77 Premium J SI1 2010 37.7152 0.77 Very Good J SI1 2010 37.4936 0.7 Ideal F SI2 2011 36.1168 0.56 Premium D VS2 2011 31.4024 0.63 Fair E VS2 2011 32.2471 0.52 Premium G VVS2 2012 29.7438 0.52 Ideal G VVS2 2012 30.0336 0.52 Ideal G VVS2 2012 29.866600000000002 0.52 Premium G VVS2 2012 29.94 0.52 Ideal G VVS2 2012 30.0623 0.52 Ideal G VVS2 2012 30.126 0.52 Ideal G VVS2 2012 30.3232 0.52 Ideal G VVS2 2012 30.7024 0.52 Ideal G VVS2 2012 29.773799999999998 0.52 Ideal G VVS2 2012 29.7124 0.52 Ideal G VVS2 2012 29.702399999999997 0.52 Premium G VVS2 2012 29.672399999999996 0.52 Ideal G VVS2 2012 29.722099999999998 0.52 Ideal G VVS2 2012 29.6192 0.52 Premium G VVS2 2012 29.6508 0.78 Ideal I VS2 2012 38.4691 0.78 Ideal H SI2 2012 38.0865 0.5 Very Good F VVS2 2013 29.1199 0.63 Ideal D VS2 2013 34.3332 0.56 Premium G VS1 2013 32.2817 0.72 Very Good G SI2 2015 35.9718 0.53 Ideal G VVS1 2015 30.667199999999998 0.57 Good D VS2 2015 32.709 0.76 Good J VS1 2015 36.355 0.71 Good D SI2 2015 37.284 0.7 Premium G SI1 2016 36.38399999999999 0.56 Premium F SI1 2016 30.799399999999995 0.8 Premium J SI1 2016 40.5148 0.54 Very Good D VS1 2016 30.423700000000004 0.55 Ideal G VVS2 2016 31.522 0.56 Ideal F VS1 2016 31.582 0.56 Ideal F VS1 2016 31.815200000000004 0.5 Ideal F VVS2 2016 29.6638 0.76 Good I SI1 2016 36.627500000000005 0.7 Good G SI1 2016 35.0058 0.7 Fair G SI1 2016 35.044000000000004 0.56 Ideal F VS1 2016 31.359600000000004 0.56 Ideal F VS1 2016 31.359600000000004 0.56 Ideal F VS1 2016 31.529 0.5 Premium F VVS2 2016 29.2217 0.5 Ideal F VVS2 2016 28.794 0.56 Premium F VS1 2016 32.245799999999996 0.6 Premium E SI1 2016 33.5296 0.66 Good F SI1 2017 34.9735 1.01 Premium I I1 2017 46.2252 0.7 Very Good H SI1 2018 37.379400000000004 0.5 Ideal F VVS1 2018 28.7942 0.55 Ideal D SI1 201

In [0]:
( 
  df_cleaned.write
  .format('json')
  .mode('overwrite')
  .save(f'/tmp/{username}/diamonds_json')
)

In [0]:
display( dbutils.fs.ls(f'/tmp/{username}/diamonds_json') )

path name size dbfs:/tmp/masahiko_kitamura_databricks_com/diamonds_json/_committed_7033217148156085684 _committed_7033217148156085684 202 dbfs:/tmp/masahiko_kitamura_databricks_com/diamonds_json/_committed_8257997043505265100 _committed_8257997043505265100 202 dbfs:/tmp/masahiko_kitamura_databricks_com/diamonds_json/_committed_vacuum4291654736168110024 _committed_vacuum4291654736168110024 96 dbfs:/tmp/masahiko_kitamura_databricks_com/diamonds_json/_started_8257997043505265100 _started_8257997043505265100 0 dbfs:/tmp/masahiko_kitamura_databricks_com/diamonds_json/part-00000-tid-8257997043505265100-c0ac53bf-7584-42ad-8753-836c9374b41f-2851-1-c000.json part-00000-tid-8257997043505265100-c0ac53bf-7584-42ad-8753-836c9374b41f-2851-1-c000.json 326089

In [0]:
%fs head dbfs:/tmp/masahiko_kitamura_databricks_com/diamonds_json/part-00000-tid-8257997043505265100-c0ac53bf-7584-42ad-8753-836c9374b41f-2851-1-c000.json

[Truncated to first 65536 bytes]
{"carat":0.59,"cut":"Very Good","color":"F","clarity":"SI1","price":2000,"magic_number":32.3}
{"carat":0.7,"cut":"Ideal","color":"J","clarity":"VS1","price":2000,"magic_number":35.4724}
{"carat":0.7,"cut":"Good","color":"E","clarity":"SI1","price":2000,"magic_number":33.7896}
{"carat":0.7,"cut":"Fair","color":"E","clarity":"SI1","price":2000,"magic_number":36.352399999999996}
{"carat":0.58,"cut":"Very Good","color":"F","clarity":"VS1","price":2001,"magic_number":31.9116}
{"carat":0.77,"cut":"Very Good","color":"J","clarity":"SI2","price":2001,"magic_number":38.8536}
{"carat":0.77,"cut":"Very Good","color":"J","clarity":"SI2","price":2001,"magic_number":38.1144}
{"carat":0.72,"cut":"Very Good","color":"G","clarity":"SI2","price":2001,"magic_number":35.9857}
{"carat":0.73,"cut":"Very Good","color":"H","clarity":"SI1","price":2001,"magic_number":37.065999999999995}
{"carat":0.55,"cut":"Ideal","color":"E","clarity":"VS1","price":2001,"magic_number":31.224000000000004}
{"carat":0.55,"cut":"Ideal","color":"E","clarity":"VS1","price":2001,"magic_number":30.8748}
{"carat":0.53,"cut":"Ideal","color":"G","clarity":"VVS1","price":2001,"magic_number":30.1778}
{"carat":0.75,"cut":"Ideal","color":"J","clarity":"VS2","price":2001,"magic_number":38.253}
{"carat":0.71,"cut":"Ideal","color":"J","clarity":"SI1","price":2001,"magic_number":36.4944}
{"carat":0.57,"cut":"Premium","color":"D","clarity":"SI1","price":2001,"magic_number":32.196000000000005}
{"carat":0.61,"cut":"Ideal","color":"F","clarity":"VS2","price":2002,"magic_number":32.929}
{"carat":0.71,"cut":"Fair","color":"E","clarity":"SI2","price":2002,"magic_number":34.631299999999996}
{"carat":0.74,"cut":"Premium","color":"E","clarity":"SI2","price":2002,"magic_number":36.9983}
{"carat":0.5,"cut":"Very Good","color":"F","clarity":"VVS2","price":2003,"magic_number":29.2208}
{"carat":0.5,"cut":"Very Good","color":"E","clarity":"VVS2","price":2003,"magic_number":29.007700000000003}
{"carat":0.74,"cut":"Very Good","color":"J","clarity":"VS2","price":2003,"magic_number":37.4115}
{"carat":0.71,"cut":"Very Good","color":"I","clarity":"SI2","price":2003,"magic_number":36.8404}
{"carat":0.54,"cut":"Very Good","color":"D","clarity":"VS1","price":2004,"magic_number":30.1042}
{"carat":0.56,"cut":"Ideal","color":"G","clarity":"VVS2","price":2004,"magic_number":31.7955}
{"carat":0.54,"cut":"Ideal","color":"D","clarity":"VS1","price":2004,"magic_number":30.3218}
{"carat":0.51,"cut":"Ideal","color":"G","clarity":"VVS1","price":2005,"magic_number":29.3112}
{"carat":0.51,"cut":"Very Good","color":"G","clarity":"VVS1","price":2005,"magic_number":30.766}
{"carat":0.51,"cut":"Ideal","color":"G","clarity":"VVS1","price":2005,"magic_number":29.403999999999996}
{"carat":0.53,"cut":"Ideal","color":"G","clarity":"VVS1","price":2005,"magic_number":30.532799999999998}
{"carat":0.53,"cut":"Ideal","color":"G","clarity":"VVS1","price":2005,"magic_number":30.146}
{"carat":0.53,"cut":"Ideal","color":"G","clarity":"VVS1","price":2005,"magic_number":30.333700000000004}
{"carat":0.7,"cut":"Premium","color":"J","clarity":"VS1","price":2005,"magic_number":35.9018}
{"carat":0.77,"cut":"Premium","color":"J","clarity":"VS1","price":2005,"magic_number":37.677}
{"carat":0.77,"cut":"Fair","color":"J","clarity":"VS1","price":2005,"magic_number":38.1136}
{"carat":0.77,"cut":"Good","color":"E","clarity":"SI2","price":2005,"magic_number":37.416799999999995}
{"carat":0.71,"cut":"Ideal","color":"H","clarity":"SI1","price":2006,"magic_number":37.0437}
{"carat":0.72,"cut":"Ideal","color":"J","clarity":"VS1","price":2006,"magic_number":36.365399999999994}
{"carat":0.71,"cut":"Premium","color":"H","clarity":"SI1","price":2006,"magic_number":36.5721}
{"carat":0.58,"cut":"Ideal","color":"H","clarity":"VVS1","price":2006,"magic_number":32.146499999999996}
{"carat":0.76,"cut":"Very Good","color":"D","clarity":"SI2","price":2006,"magic_number":37.9844}
{"carat":0.67,"cut":"Very Good","color":"D","clarity":"SI1","

In [0]:
df.createOrReplaceTempView('diamonds')

df_sql = sql('''
  SELECT 
    carat, cut, color, clarity, price, x * y + z as magic_number
  FROM diamonds
''')

display( df_sql )

carat cut color clarity price magic_number 0.23 Ideal E SI2 326 18.151 0.21 Premium E SI1 326 17.2476 0.23 Good E VS1 327 18.793499999999998 0.29 Premium I VS2 334 20.396 0.31 Good J SI2 335 21.628999999999998 0.24 Very Good J VVS2 336 18.0824 0.24 Very Good I VVS1 336 18.191 0.26 Very Good H SI1 337 19.257700000000003 0.22 Fair E VS2 337 17.1186 0.23 Very Good H VS1 338 18.59 0.3 Good J SI1 339 20.92 0.23 Ideal J VS1 340 17.787 0.22 Premium F SI1 342 17.2292 0.31 Ideal J SI2 344 21.7195 0.2 Premium E SI2 345 16.4825 0.32 Premium E I1 345 22.0396 0.3 Ideal I SI2 348 21.385399999999997 0.3 Good J SI1 351 20.846700000000002 0.3 Good J SI1 351 20.7298 0.3 Very Good J SI1 351 20.636699999999998 0.3 Good I SI2 351 21.028 0.23 Very Good E VS2 352 17.572 0.23 Very Good H VS1 353 18.0124 0.31 Very Good J SI1 353 22.0677 0.31 Very Good J SI1 353 22.4368 0.23 Very Good G VVS2 354 18.329700000000003 0.24 Premium I VS1 355 18.1118 0.3 Very Good J VS2 357 21.073999999999998 0.23 Very Good D VS2 357 18.1212 0.23 Very Good F VS1 357 18.2204 0.23 Very Good F VS1 402 18.53 0.23 Very Good F VS1 402 18.822400000000002 0.23 Very Good E VS1 402 18.3397 0.23 Very Good E VS1 402 18.680599999999995 0.23 Very Good D VS1 402 17.9632 0.23 Good F VS1 402 18.9348 0.23 Good E VS1 402 17.2055 0.31 Good H SI1 402 21.2399 0.26 Very Good D VS2 403 19.7008 0.33 Ideal I SI2 403 23.0299 0.33 Ideal I SI2 403 22.955000000000002 0.33 Ideal J SI1 403 23.189500000000002 0.26 Good D VS2 403 18.6498 0.26 Good D VS1 403 20.225600000000004 0.32 Good H SI2 403 21.7158 0.29 Premium F SI1 403 20.7124 0.32 Very Good H SI2 403 21.936999999999998 0.32 Good H SI2 403 21.8868 0.25 Very Good E VS2 404 18.66 0.29 Very Good H SI2 404 21.5621 0.24 Very Good F SI1 404 18.650599999999997 0.23 Ideal G VS1 404 17.963500000000003 0.32 Ideal I SI1 404 22.656000000000002 0.22 Premium E VS2 404 17.6977 0.22 Premium D VS2 404 17.4808 0.3 Ideal I SI2 405 21.249 0.3 Premium J SI2 405 22.013399999999997 0.3 Very Good I SI1 405 20.86 0.3 Very Good I SI1 405 21.199600000000004 0.3 Good I SI1 405 20.9325 0.35 Ideal I VS1 552 23.6186 0.3 Premium D SI1 552 20.7221 0.3 Ideal D SI1 552 21.222800000000003 0.3 Ideal D SI1 552 21.299 0.42 Premium I SI2 552 26.095200000000002 0.28 Ideal G VVS2 553 20.2618 0.32 Ideal I VVS1 553 22.133799999999997 0.31 Very Good G SI1 553 21.349 0.31 Premium G SI1 553 21.471999999999998 0.24 Premium E VVS1 553 18.6003 0.24 Very Good D VVS1 553 18.330000000000002 0.3 Very Good H SI1 554 21.018299999999996 0.3 Premium H SI1 554 20.8272 0.3 Premium H SI1 554 20.902500000000003 0.3 Good H SI1 554 20.9528 0.26 Very Good F VVS2 554 20.171799999999998 0.26 Very Good E VVS2 554 20.064500000000002 0.26 Very Good D VVS2 554 19.4104 0.26 Very Good D VVS2 554 18.7705 0.26 Very Good E VVS1 554 19.1554 0.26 Very Good E VVS1 554 18.71 0.26 Very Good D VVS1 554 19.1336 0.26 Ideal E VVS2 554 18.861199999999997 0.38 Ideal I SI2 554 24.585500000000003 0.26 Good E VVS1 554 20.384999999999998 0.24 Premium G VVS1 554 17.934 0.24 Premium H VVS1 554 18.319599999999998 0.24 Premium H VVS1 554 18.52 0.24 Premium H VVS2 554 18.902800000000003 0.32 Premium I SI1 554 21.5655 0.7 Ideal E SI1 2757 36.174 0.86 Fair E SI2 2757 44.3485 0.7 Ideal G VS2 2757 35.819 0.71 Very Good E VS2 2759 36.1064 0.78 Very Good G SI2 2759 37.708499999999994 0.7 Good E VS2 2759 37.895 0.7 Good F VS1 2759 36.2896 0.96 Fair F SI2 2759 41.3765 0.73 Very Good E SI1 2760 36.9106 0.8 Premium H SI1 2760 39.0621 0.75 Very Good D SI1 2760 37.0 0.75 Premium E SI1 2760 39.339999999999996 0.74 Ideal G SI1 2760 37.519999999999996 0.75 Premium G VS2 2760 37.4615 0.8 Ideal I VS1 2760 38.5878 0.75 Ideal G SI1 2760 37.676 0.8 Premium G SI1 2760 37.968999999999994 0.74 Ideal I VVS2 2761 37.1337 0.81 Ideal F SI2 2761 41.1154 0.59 Ideal E VVS2 2761 32.563399999999994 0.8 Ideal F SI2 2761 39.43 0.74 Ideal E SI2 2761 37.492 0.9 Premium I VS2 2761 41.5692 0.74 Very Good G SI1 2762 36.93860000000001 0.73 Ideal F VS2 2762 36.7198 0.73 Ideal F VS2 276

### 従来のデータレイクの制限と限界

-----
* ファイルのパーティションをユーザーが管理しないといけない
* 細かいファイルがどんどん増えていく
* ファイル数が増えるにつれて読み込みに時間がかかる
* レコードは追記のみ(UPDATE, DELETE, MERGEができない)
* スキーマの整合性はユーザー側でチェックしないといけない
* 検索条件がパーティションキーでない場合、全てのファイルを開く必要がある
* Indexingなどの最適化機能がない


など。

# 1. Delta Lakeの世界

### サンプルデータ

今回使用するデータはLending Clubが公開している2012年から2017年までの融資審査データです。
ローン申請者情報(匿名)、現在のローンステータス(延滞、全額支払い済みなど)などが含まれます。

**データ辞書** https://www.kaggle.com/wendykan/lending-club-loan-data <br>

<!--<img src="https://jixjiastorage.blob.core.windows.net/public/datasets/lending-club-loan/data_sample.png" width="95%">-->

In [0]:
# パス指定
source_path = 'dbfs:/databricks-datasets/samples/lending_club/parquet/'
delta_path = f'dbfs:/home/{username}/delta/lending-club-loan/'

# 既存のデータを削除
dbutils.fs.rm(delta_path, recurse=True)

# データを読み込む
df = spark.read.parquet(source_path)

# レコード数
print(df.count())

# randomSplit()を使って、5%のサンプルを読み取る
(data, data_rest) = df.randomSplit([0.05, 0.95], seed=123)

# 読み込まれたデータを参照
display( data )

1481560

id member_id loan_amnt funded_amnt funded_amnt_inv term int_rate installment grade sub_grade emp_title emp_length home_ownership annual_inc verification_status loan_status pymnt_plan url desc purpose title zip_code addr_state dti delinq_2yrs earliest_cr_line inq_last_6mths mths_since_last_delinq mths_since_last_record open_acc pub_rec revol_bal revol_util total_acc initial_list_status out_prncp out_prncp_inv total_pymnt total_pymnt_inv total_rec_prncp total_rec_int total_rec_late_fee recoveries collection_recovery_fee last_pymnt_d last_pymnt_amnt next_pymnt_d last_credit_pull_d collections_12_mths_ex_med mths_since_last_major_derog policy_code application_type annual_inc_joint dti_joint verification_status_joint acc_now_delinq tot_coll_amt tot_cur_bal open_acc_6m open_il_6m open_il_12m open_il_24m mths_since_rcnt_il total_bal_il il_util open_rv_12m open_rv_24m max_bal_bc all_util total_rev_hi_lim inq_fi total_cu_tl inq_last_12m acc_open_past_24mths avg_cur_bal bc_open_to_buy bc_util chargeoff_within_12_mths delinq_amnt mo_sin_old_il_acct mo_sin_old_rev_tl_op mo_sin_rcnt_rev_tl_op mo_sin_rcnt_tl mort_acc mths_since_recent_bc mths_since_recent_bc_dlq mths_since_recent_inq mths_since_recent_revol_delinq num_accts_ever_120_pd num_actv_bc_tl num_actv_rev_tl num_bc_sats num_bc_tl num_il_tl num_op_rev_tl num_rev_accts num_rev_tl_bal_gt_0 num_sats num_tl_120dpd_2m num_tl_30dpd num_tl_90g_dpd_24m num_tl_op_past_12m pct_tl_nvr_dlq percent_bc_gt_75 pub_rec_bankruptcies tax_liens tot_hi_cred_lim total_bal_ex_mort total_bc_limit total_il_high_credit_limit revol_bal_joint sec_app_earliest_cr_line sec_app_inq_last_6mths sec_app_mort_acc sec_app_open_acc sec_app_revol_util sec_app_open_il_6m sec_app_num_rev_accts sec_app_chargeoff_within_12_mths sec_app_collections_12_mths_ex_med sec_app_mths_since_last_major_derog hardship_flag hardship_type hardship_reason hardship_status deferral_term hardship_amount hardship_start_date hardship_end_date payment_plan_start_date hardship_length hardship_dpd hardship_loan_status orig_projected_additional_accrued_interest hardship_payoff_balance_amount hardship_last_payment_amount issue_d null null 1000.0 1000 1000.0 36 months 5.32% 30.12 A A1 Transit Property Protection Supervisor 6 years RENT 62500.0 Source Verified Current n null null moving Moving and relocation 114xx NY 25.13 0.0 Apr-2001 0 null null 14 0 6594 22.6% 19.0 w 576.27 576.27 455.49 455.49 423.73 31.76 0.0 0.0 0.0 Aug-2017 30.12 Sep-2017 Aug-2017 0 null 1 INDIVIDUAL null null null 0 0 38765 0 2 0 1 18 32171 63 0 0 3866 48 29200 2 0 0 1 2982 14134 24.8 0.0 0 84.0 187 35 18 0 35 null 18 null 0 2 5 6 6 4 12 15 5 14 0 0 0 0 100.0 0.0 0 0 80103 38765 18800 50903 null null null null null null null null null null null N null null null null null null null null null null null null null null Nov-2016 null null 1000.0 1000 1000.0 36 months 6.49% 30.65 A A2 Customers Service Consultant < 1 year RENT 40000.0 Source Verified Current n null null debt_consolidation Debt consolidation 441xx OH 24.09 0.0 Oct-2003 0 29 null 15 0 2184 19.5% 24.0 w 551.81 551.81 521.19 521.19 448.19 73.0 0.0 0.0 0.0 Aug-2017 30.65 Sep-2017 Aug-2017 0 57 1 INDIVIDUAL null null null 0 0 37821 0 11 0 1 14 35637 76 0 1 761 65 11200 0 0 0 2 2521 39 95.1 0.0 0 149.0 105 16 14 0 54 76 null 29 2 1 4 1 2 19 4 5 4 15 0 0 0 0 87.5 100.0 0 0 57980 37821 800 46780 null null null null null null null null null null null N null null null null null null null null null null null null null null Mar-2016 null null 1000.0 1000 1000.0 36 months 6.49% 30.65 A A2 dental assistant 8 years RENT 28000.0 Not Verified Current n null null credit_card Credit card refinancing 142xx NY 26.49 0.0 Sep-2004 0 null null 6 0 3651 40.1% 19.0 w 579.33 579.33 490.04 490.04 420.67 69.37 0.0 0.0 0.0 Aug-2017 30.65 Sep-2017 Aug-2017 0 null 1 INDIVIDUAL null null null 0 0 11743 0 3 0 1 13 8092 46 1 1 2697 44 9100 0 0 0 2 1957 4825 40.4 0.0 0 124.0 139 9 9 0 25 null null null 0 2 3 2 12 4 3 15 3 6 0 0 0 1 100.0 0.0 0 0 26793 

In [0]:
from pandas_profiling import ProfileReport
df_profile = ProfileReport(df.toPandas(), minimal=True, title="Profiling Report", progress_bar=False, infer_dtypes=False)
profile_html = df_profile.to_html()

displayHTML(profile_html)

In [0]:
# 簡単な処理を行い、結果をParquetとして保存
from pyspark.sql.functions import col, expr

data.select('loan_amnt', 
            'term',
            'int_rate',
            'grade',
            'addr_state',
            'emp_title',
            'home_ownership',
            'annual_inc',
            'loan_status')\
  .withColumn('int_rate', expr('cast(replace(int_rate,"%","") as float)'))\
  .withColumnRenamed('addr_state', 'state')\
  .write\
  .format('delta')\
  .mode('overwrite')\
  .save(delta_path)

In [0]:
# Databaseを作成
sql(f'CREATE DATABASE IF NOT EXISTS {dbname}')
sql(f'USE {dbname}')

# テーブルとして登録
sql(f'DROP TABLE IF EXISTS LBS')
sql(f'CREATE TABLE LBS USING delta LOCATION "{delta_path}"')

Out[26]: DataFrame[]

-sandbox
<div style="float:left; padding-right:10px; margin-top:10px;">
  <img src='https://jixjiadatabricks.blob.core.windows.net/images/data-lake-traditional.png' width='70px'>
</div>
<div style="float:left;">
  <h3>データの読み込み(クエリ)</h3>
  Parquetによる分散ファイルは<span style="color:green"><strong>効率よく読む</strong></span>事ができます</span>.
</div>

In [0]:
%sql

-- データをSELECT文でクエリしてみよう
Select state, loan_status, count(*) as counts 
From LBS  
Group by state, loan_status
Order by counts desc

state loan_status counts CA Current 4996 CA Fully Paid 4008 TX Current 3274 NY Current 3179 FL Current 2805 TX Fully Paid 2179 NY Fully Paid 2006 FL Fully Paid 1782 IL Current 1666 NJ Current 1520 OH Current 1415 PA Current 1393 GA Current 1311 VA Current 1076 MI Current 1071 NC Current 1068 IL Fully Paid 995 CA Charged Off 962 MA Current 942 MD Current 935 AZ Current 931 NJ Fully Paid 927 GA Fully Paid 856 WA Current 838 OH Fully Paid 833 PA Fully Paid 819 VA Fully Paid 788 NC Fully Paid 762 CO Current 736 MN Current 708 IN Current 694 AZ Fully Paid 686 MO Current 677 TN Current 670 MI Fully Paid 666 CO Fully Paid 657 CT Current 643 WA Fully Paid 626 MD Fully Paid 608 NY Charged Off 597 MA Fully Paid 586 WI Current 561 SC Current 550 TX Charged Off 517 FL Charged Off 513 NV Current 496 LA Current 483 MN Fully Paid 483 AL Current 470 OR Current 440 NV Fully Paid 410 MO Fully Paid 406 KY Current 406 IN Fully Paid 398 CT Fully Paid 369 OK Current 364 TN Fully Paid 344 WI Fully Paid 342 KS Current 334 OR Fully Paid 326 LA Fully Paid 311 AR Current 305 AL Fully Paid 301 SC Fully Paid 300 NJ Charged Off 285 OH Charged Off 256 PA Charged Off 255 KY Fully Paid 250 IL Charged Off 243 MS Current 243 KS Fully Paid 219 UT Current 215 UT Fully Paid 210 NH Current 207 NM Current 206 GA Charged Off 205 OK Fully Paid 204 AR Fully Paid 197 NC Charged Off 192 HI Current 188 VA Charged Off 180 HI Fully Paid 175 NM Fully Paid 168 MD Charged Off 168 AZ Charged Off 167 RI Current 157 MI Charged Off 154 NE Current 153 CA Late (31-120 days) 130 MA Charged Off 128 NH Fully Paid 128 WA Charged Off 126 AL Charged Off 125 MN Charged Off 121 CO Charged Off 120 DE Current 120 NV Charged Off 119 TN Charged Off 115 RI Fully Paid 114 MT Current 109 MO Charged Off 108 WV Fully Paid 107 ME Current 102 TX Late (31-120 days) 100 IN Charged Off 98 WY Current 96 WV Current 96 FL Late (31-120 days) 96 LA Charged Off 94 DC Current 92 MS Fully Paid 91 NY Late (31-120 days) 90 CT Charged Off 86 DC Fully Paid 83 VT Current 82 SD Current 80 AK Current 78 AK Fully Paid 77 CA In Grace Period 76 OK Charged Off 73 DE Fully Paid 72 WI Charged Off 71 MT Fully Paid 69 WY Fully Paid 67 SC Charged Off 67 ND Current 66 OR Charged Off 65 ID Current 64 NY In Grace Period 63 KY Charged Off 61 AR Charged Off 58 TX In Grace Period 58 KS Charged Off 57 SD Fully Paid 56 VT Fully Paid 48 FL In Grace Period 47 UT Charged Off 46 NM Charged Off 45 CA Late (16-30 days) 44 MS Charged Off 43 VA Late (31-120 days) 41 NJ Late (31-120 days) 41 NE Fully Paid 38 PA Late (31-120 days) 38 NC Late (31-120 days) 38 NY Late (16-30 days) 37 OH Late (31-120 days) 37 MD Late (31-120 days) 35 GA Late (31-120 days) 31 HI Charged Off 30 TX Late (16-30 days) 30 MD In Grace Period 29 IL Late (31-120 days) 28 NJ In Grace Period 27 GA In Grace Period 26 FL Late (16-30 days) 26 IL In Grace Period 25 MA Late (31-120 days) 24 RI Charged Off 24 DE Charged Off 24 MI Late (31-120 days) 23 MO Late (31-120 days) 23 OH In Grace Period 22 AZ Late (31-120 days) 22 WV Charged Off 21 MN Late (31-120 days) 20 NH Charged Off 20 VA In Grace Period 20 NV Late (31-120 days) 20 PA In Grace Period 19 WY Charged Off 19 LA Late (31-120 days) 19 CT Late (31-120 days) 17 AL Late (31-120 days) 17 MO In Grace Period 17 MI In Grace Period 16 IN Late (31-120 days) 16 NC In Grace Period 16 MT Charged Off 16 WI Late (31-120 days) 16 ME Fully Paid 15 MA In Grace Period 15 TN Late (31-120 days) 15 ND Fully Paid 15 VA Late (16-30 days) 15 NE Charged Off 14 CO Late (31-120 days) 14 WA Late (31-120 days) 14 AL In Grace Period 13 CT In Grace Period 13 SD Charged Off 13 ID Fully Paid 12 NJ Late (16-30 days) 12 AK Charged Off 12 MN In Grace Period 12 DC Charged Off 12 CO In Grace Period 11 SC In Grace Period 11 AZ In Grace Period 10 IL Late (16-30 days) 10 SC Late (31-120 days) 10 KS Late (31-120 days) 10 MS Late (31-120 days) 10 LA In Grace Period 10 WI In Grace Period 10 KY Late (31-120 days) 10 IN In Grace Period 9 OK Late (31-120 days) 9 HI Late 

-sandbox
<div style="float:left; padding-right:10px; margin-top:10px;">
  <img src='https://jixjiadatabricks.blob.core.windows.net/images/data-lake-no-label.png' width='70px'>
</div>
<div style="float:left;">
  <h3>Deltaの物理的な構造</h3>
  Delta LakeはParquet技術の上に成り立っています
</div>

In [0]:
# %fs ls /home/{username}/delta/lending-club-loan/

display( 
  dbutils.fs.ls(f'{delta_path}') # <= Deltaを書き込んだディレクトリをリストしてみる
)

path name size dbfs:/home/masahiko_kitamura_databricks_com/delta/lending-club-loan/_delta_log/ _delta_log/ 0 dbfs:/home/masahiko_kitamura_databricks_com/delta/lending-club-loan/part-00000-f949f076-1271-425e-ba22-70eaad7662cf-c000.snappy.parquet part-00000-f949f076-1271-425e-ba22-70eaad7662cf-c000.snappy.parquet 339369 dbfs:/home/masahiko_kitamura_databricks_com/delta/lending-club-loan/part-00001-0b1ad511-7319-46b4-9be7-b124e8be813f-c000.snappy.parquet part-00001-0b1ad511-7319-46b4-9be7-b124e8be813f-c000.snappy.parquet 285179 dbfs:/home/masahiko_kitamura_databricks_com/delta/lending-club-loan/part-00002-964c046b-2377-4fbd-9c0d-cec0c915eda7-c000.snappy.parquet part-00002-964c046b-2377-4fbd-9c0d-cec0c915eda7-c000.snappy.parquet 247883 dbfs:/home/masahiko_kitamura_databricks_com/delta/lending-club-loan/part-00003-a03e2bbe-f9cf-48d2-831b-bbdb254f9276-c000.snappy.parquet part-00003-a03e2bbe-f9cf-48d2-831b-bbdb254f9276-c000.snappy.parquet 135496

In [0]:
# %fs head /home/parquet/lending-club-loan/_delta_log/00000000000000000000.json

dbutils.fs.head(f'{delta_path}/_delta_log/00000000000000000000.json')

Out[28]: '{"protocol":{"minReaderVersion":1,"minWriterVersion":2}}\n{"metaData":{"id":"fb7a843e-8b2e-4c53-b2c8-27b707c4f900","format":{"provider":"parquet","options":{}},"schemaString":"{\\"type\\":\\"struct\\",\\"fields\\":[{\\"name\\":\\"loan_amnt\\",\\"type\\":\\"float\\",\\"nullable\\":true,\\"metadata\\":{}},{\\"name\\":\\"term\\",\\"type\\":\\"string\\",\\"nullable\\":true,\\"metadata\\":{}},{\\"name\\":\\"int_rate\\",\\"type\\":\\"float\\",\\"nullable\\":true,\\"metadata\\":{}},{\\"name\\":\\"grade\\",\\"type\\":\\"string\\",\\"nullable\\":true,\\"metadata\\":{}},{\\"name\\":\\"state\\",\\"type\\":\\"string\\",\\"nullable\\":true,\\"metadata\\":{}},{\\"name\\":\\"emp_title\\",\\"type\\":\\"string\\",\\"nullable\\":true,\\"metadata\\":{}},{\\"name\\":\\"home_ownership\\",\\"type\\":\\"string\\",\\"nullable\\":true,\\"metadata\\":{}},{\\"name\\":\\"annual_inc\\",\\"type\\":\\"float\\",\\"nullable\\":true,\\"metadata\\":{}},{\\"name\\":\\"loan_status\\",\\"type\\":\\"string\\",\\"nullable\\":true,\\"metadata\\":{}}]}","partitionColumns":[],"configuration":{},"createdTime":1638968661063}}\n{"add":{"path":"part-00000-f949f076-1271-425e-ba22-70eaad7662cf-c000.snappy.parquet","partitionValues":{},"size":339369,"modificationTime":1638968671000,"dataChange":true,"stats":"{\\"numRecords\\":28120,\\"minValues\\":{\\"loan_amnt\\":1000.0,\\"term\\":\\" 36 months\\",\\"int_rate\\":5.32,\\"grade\\":\\"A\\",\\"state\\":\\"AK\\",\\"emp_title\\":\\" Business manager \\",\\"home_ownership\\":\\"ANY\\",\\"annual_inc\\":0.0,\\"loan_status\\":\\"Charged Off\\"},\\"maxValues\\":{\\"loan_amnt\\":40000.0,\\"term\\":\\" 60 months\\",\\"int_rate\\":30.99,\\"grade\\":\\"G\\",\\"state\\":\\"WY\\",\\"emp_title\\":\\"yarn operator\\",\\"home_ownership\\":\\"RENT\\",\\"annual_inc\\":1400006.0,\\"loan_status\\":\\"Late (31-120 days)\\"},\\"nullCount\\":{\\"loan_amnt\\":0,\\"term\\":0,\\"int_rate\\":0,\\"grade\\":0,\\"state\\":0,\\"emp_title\\":1847,\\"home_ownership\\":0,\\"annual_inc\\":0,\\"loan_status\\":0}}","tags":{"INSERTION_TIME":"1638968667000000","OPTIMIZE_TARGET_SIZE":"268435456"}}}\n{"add":{"path":"part-00001-0b1ad511-7319-46b4-9be7-b124e8be813f-c000.snappy.parquet","partitionValues":{},"size":285179,"modificationTime":1638968671000,"dataChange":true,"stats":"{\\"numRecords\\":23029,\\"minValues\\":{\\"loan_amnt\\":1000.0,\\"term\\":\\" 36 months\\",\\"int_rate\\":5.32,\\"grade\\":\\"A\\",\\"state\\":\\"AK\\",\\"emp_title\\":\\" GOVERNMENT ACCOUNT SPECIALIST\\",\\"home_ownership\\":\\"ANY\\",\\"annual_inc\\":0.0,\\"loan_status\\":\\"Charged Off\\"},\\"maxValues\\":{\\"loan_amnt\\":40000.0,\\"term\\":\\" 60 months\\",\\"int_rate\\":30.99,\\"grade\\":\\"G\\",\\"state\\":\\"WY\\",\\"emp_title\\":\\"yoga instructor\\",\\"home_ownership\\":\\"RENT\\",\\"annual_inc\\":4800000.0,\\"loan_status\\":\\"Late (31-120 days)\\"},\\"nullCount\\":{\\"loan_amnt\\":0,\\"term\\":0,\\"int_rate\\":0,\\"grade\\":0,\\"state\\":0,\\"emp_title\\":1298,\\"home_ownership\\":0,\\"annual_inc\\":0,\\"loan_status\\":0}}","tags":{"INSERTION_TIME":"1638968667000001","OPTIMIZE_TARGET_SIZE":"268435456"}}}\n{"add":{"path":"part-00002-964c046b-2377-4fbd-9c0d-cec0c915eda7-c000.snappy.parquet","partitionValues":{},"size":247883,"modificationTime":1638968669000,"dataChange":true,"stats":"{\\"numRecords\\":16157,\\"minValues\\":{\\"loan_amnt\\":1000.0,\\"term\\":\\" 36 months\\",\\"int_rate\\":5.32,\\"grade\\":\\"A\\",\\"state\\":\\"AK\\",\\"emp_title\\":\\" \\",\\"home_ownership\\":\\"MORTGAGE\\",\\"annual_inc\\":7000.0,\\"loan_status\\":\\"Charged Off\\"},\\"maxValues\\":{\\"loan_amnt\\":40000.0,\\"term\\":\\" 60 months\\",\\"int_rate\\":30.99,\\"grade\\":\\"G\\",\\"state\\":\\"WY\\",\\"emp_title\\":\\"zulily\\",\\"home_ownership\\":\\"RENT\\",\\"annual_inc\\":1200000.0,\\"loan_status\\":\\"Late (31-120 days)\\"},\\"nullCount\\":{\\"loan_amnt\\":0,\\"term\\":0,\\"int_rate\\":0,\\"grade\\":0,\\"state\\":0,\\"emp_title\\":971,\\"home_ownership\\":0,\\"annual_inc\\":0,\\"loan_status

In [0]:
%sql
-- Describe History機能でデータの変更履歴を監査
Describe History LBS

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata 0 2021-12-08T13:04:31.000+0000 102428 masahiko.kitamura@databricks.com WRITE Map(mode -> Overwrite, partitionBy -> []) null List(10034168) 0804-214524-boded127 null WriteSerializable false Map(numFiles -> 4, numOutputBytes -> 1007927, numOutputRows -> 74268) null

-sandbox
<div style="float:left; padding-right:10px; margin-top:20px;">
  <img src='https://jixjiadatabricks.blob.core.windows.net/images/data-lake-no-label.png' width='70px'>
</div>
<div style="float:left;">
  <h3>DMLサポート</h3>
  ここで従来のデータレイクでは出来なかった<br>データの<span style="color:green"><strong>更新</strong></span>、<span style="color:green"><strong>マージ</strong></span>や<span style="color:green"><strong>削除</strong></span>などのETL操作を行ってみたいと思います
</div>

In [0]:
%sql
-- マップで州ごとの融資総額を見てみよう
Select *
From LBS

loan_amnt term int_rate grade state emp_title home_ownership annual_inc loan_status 1000.0 36 months 5.32 A NY Transit Property Protection Supervisor RENT 62500.0 Current 1000.0 36 months 6.49 A OH Customers Service Consultant RENT 40000.0 Current 1000.0 36 months 6.49 A NY dental assistant RENT 28000.0 Current 1000.0 36 months 6.99 A TN Manager OWN 100000.0 Fully Paid 1000.0 36 months 7.24 A CA Administrative assistant MORTGAGE 48000.0 Current 1000.0 36 months 7.24 A IL Busser/Expo OWN 12000.0 Current 1000.0 36 months 7.49 A CO Teacher MORTGAGE 90000.0 Current 1000.0 36 months 8.18 B CO Admin Officer MORTGAGE 87000.0 Current 1000.0 36 months 8.24 B NY Regional Account Manager OWN 72000.0 Current 1000.0 36 months 8.24 B VA Sales,delivery RENT 44000.0 Current 1000.0 36 months 8.38 B VA Attorney MORTGAGE 110000.0 Current 1000.0 36 months 8.39 B MD Computer Technician MORTGAGE 46500.0 Fully Paid 1000.0 36 months 8.49 B NJ Sales RENT 100000.0 Current 1000.0 36 months 9.17 B VA Inside sales RENT 45000.0 Fully Paid 1000.0 36 months 9.75 B CA Police officer MORTGAGE 90000.0 Fully Paid 1000.0 36 months 9.76 B UT null MORTGAGE 37000.0 Fully Paid 1000.0 36 months 9.76 B NY Exec. Asst. OWN 74000.0 Fully Paid 1000.0 36 months 9.99 B VA Transplant Immunology Technologist MORTGAGE 50000.0 Fully Paid 1000.0 36 months 9.99 B NC registered nurse MORTGAGE 64000.0 Fully Paid 1000.0 36 months 10.49 B SC office manager MORTGAGE 36000.0 Current 1000.0 36 months 10.49 B AR Manager OWN 17000.0 Fully Paid 1000.0 36 months 10.64 B CA School Psychologist OWN 100380.0 Charged Off 1000.0 36 months 10.78 B KS Intensive supervision officer RENT 27000.0 Current 1000.0 36 months 10.78 B LA Registered nurse OWN 62000.0 Current 1000.0 36 months 10.99 B TX Claims Adjuster RENT 50000.0 Fully Paid 1000.0 36 months 10.99 B TX Sales Manager RENT 50000.0 Fully Paid 1000.0 36 months 11.22 B FL null RENT 30000.0 Current 1000.0 36 months 11.39 B NY Director of Operations RENT 70000.0 Current 1000.0 36 months 11.39 B CA Teacher MORTGAGE 75000.0 Current 1000.0 36 months 11.44 B IN Driver MORTGAGE 69000.0 Fully Paid 1000.0 36 months 11.44 B PA Food Service Instructor MORTGAGE 60000.0 Fully Paid 1000.0 36 months 11.44 B SC Picker RENT 25000.0 Fully Paid 1000.0 36 months 11.44 B FL Shipper OWN 32000.0 Current 1000.0 36 months 11.44 B NC project coordinator RENT 42000.0 Current 1000.0 36 months 11.47 B CA Legal Secretary OWN 31000.0 Fully Paid 1000.0 36 months 11.48 B AZ Public Safety Supervisor RENT 95000.0 Fully Paid 1000.0 36 months 11.48 B TX SALVAGE INVENTORY SPECIALIST RENT 48000.0 Current 1000.0 36 months 11.49 B IN null RENT 7700.0 Fully Paid 1000.0 36 months 11.49 B CA null RENT 64800.0 Current 1000.0 36 months 11.49 B MS Administrative Assistant MORTGAGE 32000.0 Current 1000.0 36 months 11.49 B CA CSR RENT 36969.0 Fully Paid 1000.0 36 months 11.49 B AZ Production Manager OWN 60000.0 Late (16-30 days) 1000.0 36 months 11.49 B MD Senior Research Manager RENT 95000.0 Fully Paid 1000.0 36 months 11.99 C FL Adjunct faculty RENT 26000.0 Fully Paid 1000.0 36 months 11.99 C IL optical tachnician RENT 40000.0 Fully Paid 1000.0 36 months 12.29 C OH District Manager MORTGAGE 41600.0 Fully Paid 1000.0 36 months 12.49 B TX Assistant Principal RENT 61000.0 Fully Paid 1000.0 36 months 12.62 C NY Sales associate RENT 12000.0 Current 1000.0 36 months 12.74 C TN Site Support Technician OWN 38400.0 Current 1000.0 36 months 12.74 C KY team member RENT 40000.0 Current 1000.0 36 months 12.79 C TX Night manager RENT 22000.0 Current 1000.0 36 months 12.99 C MD INSIDE SALES REP RENT 53000.0 Current 1000.0 36 months 12.99 C NY case manager/counselor RENT 35000.0 Fully Paid 1000.0 36 months 12.99 C PA Recruiting & Sales Delivery Manager MORTGAGE 94000.0 Current 1000.0 36 months 13.18 C OH Payroll Administrator RENT 35360.0 Current 1000.0 36 months 13.18 C NJ Payroll Coordinator RENT 62000.0 Fully Paid 1000.0 36 months 13.18 C CO senior material handler MORTGAGE 38000.0 Fully Paid 1000.0 36 mo

In [0]:
%sql
-- 'WA'州を削除する
Delete From LBS Where State = 'WA';

-- データを見る
Select * 
From LBS

loan_amnt term int_rate grade state emp_title home_ownership annual_inc loan_status 1000.0 36 months 5.32 A NY Transit Property Protection Supervisor RENT 62500.0 Current 1000.0 36 months 6.49 A OH Customers Service Consultant RENT 40000.0 Current 1000.0 36 months 6.49 A NY dental assistant RENT 28000.0 Current 1000.0 36 months 6.99 A TN Manager OWN 100000.0 Fully Paid 1000.0 36 months 7.24 A CA Administrative assistant MORTGAGE 48000.0 Current 1000.0 36 months 7.24 A IL Busser/Expo OWN 12000.0 Current 1000.0 36 months 7.49 A CO Teacher MORTGAGE 90000.0 Current 1000.0 36 months 8.18 B CO Admin Officer MORTGAGE 87000.0 Current 1000.0 36 months 8.24 B NY Regional Account Manager OWN 72000.0 Current 1000.0 36 months 8.24 B VA Sales,delivery RENT 44000.0 Current 1000.0 36 months 8.38 B VA Attorney MORTGAGE 110000.0 Current 1000.0 36 months 8.39 B MD Computer Technician MORTGAGE 46500.0 Fully Paid 1000.0 36 months 8.49 B NJ Sales RENT 100000.0 Current 1000.0 36 months 9.17 B VA Inside sales RENT 45000.0 Fully Paid 1000.0 36 months 9.75 B CA Police officer MORTGAGE 90000.0 Fully Paid 1000.0 36 months 9.76 B UT null MORTGAGE 37000.0 Fully Paid 1000.0 36 months 9.76 B NY Exec. Asst. OWN 74000.0 Fully Paid 1000.0 36 months 9.99 B VA Transplant Immunology Technologist MORTGAGE 50000.0 Fully Paid 1000.0 36 months 9.99 B NC registered nurse MORTGAGE 64000.0 Fully Paid 1000.0 36 months 10.49 B SC office manager MORTGAGE 36000.0 Current 1000.0 36 months 10.49 B AR Manager OWN 17000.0 Fully Paid 1000.0 36 months 10.64 B CA School Psychologist OWN 100380.0 Charged Off 1000.0 36 months 10.78 B KS Intensive supervision officer RENT 27000.0 Current 1000.0 36 months 10.78 B LA Registered nurse OWN 62000.0 Current 1000.0 36 months 10.99 B TX Claims Adjuster RENT 50000.0 Fully Paid 1000.0 36 months 10.99 B TX Sales Manager RENT 50000.0 Fully Paid 1000.0 36 months 11.22 B FL null RENT 30000.0 Current 1000.0 36 months 11.39 B NY Director of Operations RENT 70000.0 Current 1000.0 36 months 11.39 B CA Teacher MORTGAGE 75000.0 Current 1000.0 36 months 11.44 B IN Driver MORTGAGE 69000.0 Fully Paid 1000.0 36 months 11.44 B PA Food Service Instructor MORTGAGE 60000.0 Fully Paid 1000.0 36 months 11.44 B SC Picker RENT 25000.0 Fully Paid 1000.0 36 months 11.44 B FL Shipper OWN 32000.0 Current 1000.0 36 months 11.44 B NC project coordinator RENT 42000.0 Current 1000.0 36 months 11.47 B CA Legal Secretary OWN 31000.0 Fully Paid 1000.0 36 months 11.48 B AZ Public Safety Supervisor RENT 95000.0 Fully Paid 1000.0 36 months 11.48 B TX SALVAGE INVENTORY SPECIALIST RENT 48000.0 Current 1000.0 36 months 11.49 B IN null RENT 7700.0 Fully Paid 1000.0 36 months 11.49 B CA null RENT 64800.0 Current 1000.0 36 months 11.49 B MS Administrative Assistant MORTGAGE 32000.0 Current 1000.0 36 months 11.49 B CA CSR RENT 36969.0 Fully Paid 1000.0 36 months 11.49 B AZ Production Manager OWN 60000.0 Late (16-30 days) 1000.0 36 months 11.49 B MD Senior Research Manager RENT 95000.0 Fully Paid 1000.0 36 months 11.99 C FL Adjunct faculty RENT 26000.0 Fully Paid 1000.0 36 months 11.99 C IL optical tachnician RENT 40000.0 Fully Paid 1000.0 36 months 12.29 C OH District Manager MORTGAGE 41600.0 Fully Paid 1000.0 36 months 12.49 B TX Assistant Principal RENT 61000.0 Fully Paid 1000.0 36 months 12.62 C NY Sales associate RENT 12000.0 Current 1000.0 36 months 12.74 C TN Site Support Technician OWN 38400.0 Current 1000.0 36 months 12.74 C KY team member RENT 40000.0 Current 1000.0 36 months 12.79 C TX Night manager RENT 22000.0 Current 1000.0 36 months 12.99 C MD INSIDE SALES REP RENT 53000.0 Current 1000.0 36 months 12.99 C NY case manager/counselor RENT 35000.0 Fully Paid 1000.0 36 months 12.99 C PA Recruiting & Sales Delivery Manager MORTGAGE 94000.0 Current 1000.0 36 months 13.18 C OH Payroll Administrator RENT 35360.0 Current 1000.0 36 months 13.18 C NJ Payroll Coordinator RENT 62000.0 Fully Paid 1000.0 36 months 13.18 C CO senior material handler MORTGAGE 38000.0 Fully Paid 1000.0 36 mo

In [0]:
%sql
-- 'NY'州のローン申込額を20倍にする!
Update LBS Set loan_amnt = loan_amnt * 20 Where State = 'NY';

-- データを見る
Select *
From LBS 

-sandbox 
<div style="float:left; padding-right:40px;">
  <h4>従来のデータレイク (7 ステップ)</h4>
  <ol style="padding-left: 20px;">
    <li>更新するデータを取得 (新規データ)</li>
    <li>更新されるデータを取得 (既存データ)</li>
    <li>更新されないデータを取得 (既存データ)</li>
    <li>それぞれのTempテーブルを用意</li>
    <li>既存データを全て削除(分散物理ファイルも含めて)</li>
    <li>一つのテーブルへ合併し、元のテーブル名へ再命名</li>
    <li>Tempテーブルをドロップ</li>
   </ol>
</div>
<div style="float:left;">
  <img src="https://pages.databricks.com/rs/094-YMS-629/images/merge-into-legacy.gif" width="800px">
</div>
<div style="clear:both; display:block;">
  <h4>Delta Lake (2 ステップ)</h4>
  <ol style="padding-left: 20px;">
    <li>更新するデータを取得 (新規データ)</li>
    <li>`MERGE INTO`実行</li>
   </ol>
</div>

In [0]:
# Demo用のマージするデータを別途作成 (本番環境では新規データがこれに値する)
columns = sql('Describe Table LBS').filter('data_type != ""').select('col_name').rdd.flatMap(lambda x: x).collect()

merge_df = sc.parallelize([
   [999999, '36 months', 5.00, 'A', 'IA', 'Demo Data', 'RENT', 1000000, 'Current']
]).toDF(columns)

merge_df.createOrReplaceTempView("merge_table")
display(merge_df)

loan_amnt term int_rate grade state emp_title home_ownership annual_inc loan_status 999999 36 months 5.0 A IA Demo Data RENT 1000000 Current

In [0]:
%sql
-- マージオペレーションを行う
Merge Into LBS as target
Using merge_table as source
on target.State = source.State
when MATCHED Then Update Set *
When Not MATCHED Then Insert *
;

-- データを見る
Select *
From LBS 

loan_amnt term int_rate grade state emp_title home_ownership annual_inc loan_status 1000.0 36 months 5.32 A NY Transit Property Protection Supervisor RENT 62500.0 Current 1000.0 36 months 6.49 A OH Customers Service Consultant RENT 40000.0 Current 1000.0 36 months 6.49 A NY dental assistant RENT 28000.0 Current 1000.0 36 months 6.99 A TN Manager OWN 100000.0 Fully Paid 1000.0 36 months 7.24 A CA Administrative assistant MORTGAGE 48000.0 Current 1000.0 36 months 7.24 A IL Busser/Expo OWN 12000.0 Current 1000.0 36 months 7.49 A CO Teacher MORTGAGE 90000.0 Current 1000.0 36 months 8.18 B CO Admin Officer MORTGAGE 87000.0 Current 1000.0 36 months 8.24 B NY Regional Account Manager OWN 72000.0 Current 1000.0 36 months 8.24 B VA Sales,delivery RENT 44000.0 Current 1000.0 36 months 8.38 B VA Attorney MORTGAGE 110000.0 Current 1000.0 36 months 8.39 B MD Computer Technician MORTGAGE 46500.0 Fully Paid 1000.0 36 months 8.49 B NJ Sales RENT 100000.0 Current 1000.0 36 months 9.17 B VA Inside sales RENT 45000.0 Fully Paid 1000.0 36 months 9.75 B CA Police officer MORTGAGE 90000.0 Fully Paid 1000.0 36 months 9.76 B UT null MORTGAGE 37000.0 Fully Paid 1000.0 36 months 9.76 B NY Exec. Asst. OWN 74000.0 Fully Paid 1000.0 36 months 9.99 B VA Transplant Immunology Technologist MORTGAGE 50000.0 Fully Paid 1000.0 36 months 9.99 B NC registered nurse MORTGAGE 64000.0 Fully Paid 1000.0 36 months 10.49 B SC office manager MORTGAGE 36000.0 Current 1000.0 36 months 10.49 B AR Manager OWN 17000.0 Fully Paid 1000.0 36 months 10.64 B CA School Psychologist OWN 100380.0 Charged Off 1000.0 36 months 10.78 B KS Intensive supervision officer RENT 27000.0 Current 1000.0 36 months 10.78 B LA Registered nurse OWN 62000.0 Current 1000.0 36 months 10.99 B TX Claims Adjuster RENT 50000.0 Fully Paid 1000.0 36 months 10.99 B TX Sales Manager RENT 50000.0 Fully Paid 1000.0 36 months 11.22 B FL null RENT 30000.0 Current 1000.0 36 months 11.39 B NY Director of Operations RENT 70000.0 Current 1000.0 36 months 11.39 B CA Teacher MORTGAGE 75000.0 Current 1000.0 36 months 11.44 B IN Driver MORTGAGE 69000.0 Fully Paid 1000.0 36 months 11.44 B PA Food Service Instructor MORTGAGE 60000.0 Fully Paid 1000.0 36 months 11.44 B SC Picker RENT 25000.0 Fully Paid 1000.0 36 months 11.44 B FL Shipper OWN 32000.0 Current 1000.0 36 months 11.44 B NC project coordinator RENT 42000.0 Current 1000.0 36 months 11.47 B CA Legal Secretary OWN 31000.0 Fully Paid 1000.0 36 months 11.48 B AZ Public Safety Supervisor RENT 95000.0 Fully Paid 1000.0 36 months 11.48 B TX SALVAGE INVENTORY SPECIALIST RENT 48000.0 Current 1000.0 36 months 11.49 B IN null RENT 7700.0 Fully Paid 1000.0 36 months 11.49 B CA null RENT 64800.0 Current 1000.0 36 months 11.49 B MS Administrative Assistant MORTGAGE 32000.0 Current 1000.0 36 months 11.49 B CA CSR RENT 36969.0 Fully Paid 1000.0 36 months 11.49 B AZ Production Manager OWN 60000.0 Late (16-30 days) 1000.0 36 months 11.49 B MD Senior Research Manager RENT 95000.0 Fully Paid 1000.0 36 months 11.99 C FL Adjunct faculty RENT 26000.0 Fully Paid 1000.0 36 months 11.99 C IL optical tachnician RENT 40000.0 Fully Paid 1000.0 36 months 12.29 C OH District Manager MORTGAGE 41600.0 Fully Paid 1000.0 36 months 12.49 B TX Assistant Principal RENT 61000.0 Fully Paid 1000.0 36 months 12.62 C NY Sales associate RENT 12000.0 Current 1000.0 36 months 12.74 C TN Site Support Technician OWN 38400.0 Current 1000.0 36 months 12.74 C KY team member RENT 40000.0 Current 1000.0 36 months 12.79 C TX Night manager RENT 22000.0 Current 1000.0 36 months 12.99 C MD INSIDE SALES REP RENT 53000.0 Current 1000.0 36 months 12.99 C NY case manager/counselor RENT 35000.0 Fully Paid 1000.0 36 months 12.99 C PA Recruiting & Sales Delivery Manager MORTGAGE 94000.0 Current 1000.0 36 months 13.18 C OH Payroll Administrator RENT 35360.0 Current 1000.0 36 months 13.18 C NJ Payroll Coordinator RENT 62000.0 Fully Paid 1000.0 36 months 13.18 C CO senior material handler MORTGAGE 38000.0 Fully Paid 1000.0 36 mo

-sandbox
<div style="float:left; padding-right:10px; margin-top:20px;">
  <img src='https://jixjiadatabricks.blob.core.windows.net/images/data-lake-no-label.png' width='70px'>
</div>
<div style="float:left;">
  <h3>データ品質管理がらくらく</h3>
  スキーマエンフォースで既存のスキーマと一致しないDML操作を<span style="color:green"><strong>拒否</strong></span><br>もしくはスキーマエボリューションでスキーマの差分を<span style="color:green"><strong>完璧にマージ</strong></span>する事ができる
</div>

In [0]:
# 既存のデータの10行を読み込んで、新たなカラムを追加
new_df = spark.read\
              .format('delta')\
              .load(delta_path)\
              .limit(10)\
              .withColumn('interest_flag', expr('case when int_rate >=6 then "high" else "low" end'))

display(new_df)

loan_amnt term int_rate grade state emp_title home_ownership annual_inc loan_status interest_flag 1000.0 36 months 5.32 A NY Transit Property Protection Supervisor RENT 62500.0 Current low 1000.0 36 months 6.49 A OH Customers Service Consultant RENT 40000.0 Current high 1000.0 36 months 6.49 A NY dental assistant RENT 28000.0 Current high 1000.0 36 months 6.99 A TN Manager OWN 100000.0 Fully Paid high 1000.0 36 months 7.24 A CA Administrative assistant MORTGAGE 48000.0 Current high 1000.0 36 months 7.24 A IL Busser/Expo OWN 12000.0 Current high 1000.0 36 months 7.49 A CO Teacher MORTGAGE 90000.0 Current high 1000.0 36 months 8.18 B CO Admin Officer MORTGAGE 87000.0 Current high 1000.0 36 months 8.24 B NY Regional Account Manager OWN 72000.0 Current high 1000.0 36 months 8.24 B VA Sales,delivery RENT 44000.0 Current high

In [0]:
# スキーマが違うデータセットへ書き込む (Append)
new_df.write.format('delta').mode('append').save(delta_path)

--------------------------------------------------------------------------- 
 AnalysisException Traceback (most recent call last)
 <command-11928850> in <module> 
 1 # スキーマが違うデータセットへ書き込む (Append) 
 ----> 2 new_df . write . format ( 'delta' ) . mode ( 'append' ) . save ( delta_path ) 

 /databricks/spark/python/pyspark/sql/readwriter.py in save (self, path, format, mode, partitionBy, **options) 
 1134 self . _jwrite . save ( ) 
 1135 else : 
 -> 1136 self . _jwrite . save ( path ) 
 1137 
 1138 @ since ( 1.4 ) 

 /databricks/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py in __call__ (self, *args) 
 1302 
 1303 answer = self . gateway_client . send_command ( command ) 
 -> 1304 return_value = get_return_value(
 1305 answer, self.gateway_client, self.target_id, self.name)
 1306 

 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 121 # Hide where the exception came from that shows a non-Pythonic 
 122 # JVM exception message. 
 --> 123 raise converted from None 
 124 else : 
 125 raise 

 AnalysisException : A schema mismatch detected when writing to the Delta table (Table ID: fb7a843e-8b2e-4c53-b2c8-27b707c4f900).
To enable schema migration using DataFrameWriter or DataStreamWriter, please set:
'.option("mergeSchema", "true")'.
For other operations, set the session configuration
spark.databricks.delta.schema.autoMerge.enabled to "true". See the documentation
specific to the operation for details.

Table schema:
root
-- loan_amnt: float (nullable = true)
-- term: string (nullable = true)
-- int_rate: float (nullable = true)
-- grade: string (nullable = true)
-- state: string (nullable = true)
-- emp_title: string (nullable = true)
-- home_ownership: string (nullable = true)
-- annual_inc: float (nullable = true)
-- loan_status: string (nullable = true)


Data schema:
root
-- loan_amnt: float (nullable = true)
-- term: string (nullable = true)
-- int_rate: float (nullable = true)
-- grade: string (nullable = true)
-- state: string (nullable = true)
-- emp_title: string (nullable = true)
-- home_ownership: string (nullable = true)
-- annual_inc: float (nullable = true)
-- loan_status: string (nullable = true)
-- interest_flag: string (nullable = true)

今度は`mergeSchema`オプションを使って異なるスキーマ同士のデータを融合させましょう（スキーマエボリューション)

In [0]:
# スキーマが違うデータセットへ書き込む (with スキーマエボリューション)
new_df.write.format('delta').option('mergeSchema','true').mode('append').save(delta_path)

In [0]:
%sql
describe LBS

col_name data_type comment loan_amnt float term string int_rate float grade string state string emp_title string home_ownership string annual_inc float loan_status string interest_flag string # Partitioning Not partitioned

In [0]:
%sql
-- データを見る
Select *
From LBS 

loan_amnt term int_rate grade state emp_title home_ownership annual_inc loan_status interest_flag 1000.0 36 months 5.32 A NY Transit Property Protection Supervisor RENT 62500.0 Current null 1000.0 36 months 6.49 A OH Customers Service Consultant RENT 40000.0 Current null 1000.0 36 months 6.49 A NY dental assistant RENT 28000.0 Current null 1000.0 36 months 6.99 A TN Manager OWN 100000.0 Fully Paid null 1000.0 36 months 7.24 A CA Administrative assistant MORTGAGE 48000.0 Current null 1000.0 36 months 7.24 A IL Busser/Expo OWN 12000.0 Current null 1000.0 36 months 7.49 A CO Teacher MORTGAGE 90000.0 Current null 1000.0 36 months 8.18 B CO Admin Officer MORTGAGE 87000.0 Current null 1000.0 36 months 8.24 B NY Regional Account Manager OWN 72000.0 Current null 1000.0 36 months 8.24 B VA Sales,delivery RENT 44000.0 Current null 1000.0 36 months 8.38 B VA Attorney MORTGAGE 110000.0 Current null 1000.0 36 months 8.39 B MD Computer Technician MORTGAGE 46500.0 Fully Paid null 1000.0 36 months 8.49 B NJ Sales RENT 100000.0 Current null 1000.0 36 months 9.17 B VA Inside sales RENT 45000.0 Fully Paid null 1000.0 36 months 9.75 B CA Police officer MORTGAGE 90000.0 Fully Paid null 1000.0 36 months 9.76 B UT null MORTGAGE 37000.0 Fully Paid null 1000.0 36 months 9.76 B NY Exec. Asst. OWN 74000.0 Fully Paid null 1000.0 36 months 9.99 B VA Transplant Immunology Technologist MORTGAGE 50000.0 Fully Paid null 1000.0 36 months 9.99 B NC registered nurse MORTGAGE 64000.0 Fully Paid null 1000.0 36 months 10.49 B SC office manager MORTGAGE 36000.0 Current null 1000.0 36 months 10.49 B AR Manager OWN 17000.0 Fully Paid null 1000.0 36 months 10.64 B CA School Psychologist OWN 100380.0 Charged Off null 1000.0 36 months 10.78 B KS Intensive supervision officer RENT 27000.0 Current null 1000.0 36 months 10.78 B LA Registered nurse OWN 62000.0 Current null 1000.0 36 months 10.99 B TX Claims Adjuster RENT 50000.0 Fully Paid null 1000.0 36 months 10.99 B TX Sales Manager RENT 50000.0 Fully Paid null 1000.0 36 months 11.22 B FL null RENT 30000.0 Current null 1000.0 36 months 11.39 B NY Director of Operations RENT 70000.0 Current null 1000.0 36 months 11.39 B CA Teacher MORTGAGE 75000.0 Current null 1000.0 36 months 11.44 B IN Driver MORTGAGE 69000.0 Fully Paid null 1000.0 36 months 11.44 B PA Food Service Instructor MORTGAGE 60000.0 Fully Paid null 1000.0 36 months 11.44 B SC Picker RENT 25000.0 Fully Paid null 1000.0 36 months 11.44 B FL Shipper OWN 32000.0 Current null 1000.0 36 months 11.44 B NC project coordinator RENT 42000.0 Current null 1000.0 36 months 11.47 B CA Legal Secretary OWN 31000.0 Fully Paid null 1000.0 36 months 11.48 B AZ Public Safety Supervisor RENT 95000.0 Fully Paid null 1000.0 36 months 11.48 B TX SALVAGE INVENTORY SPECIALIST RENT 48000.0 Current null 1000.0 36 months 11.49 B IN null RENT 7700.0 Fully Paid null 1000.0 36 months 11.49 B CA null RENT 64800.0 Current null 1000.0 36 months 11.49 B MS Administrative Assistant MORTGAGE 32000.0 Current null 1000.0 36 months 11.49 B CA CSR RENT 36969.0 Fully Paid null 1000.0 36 months 11.49 B AZ Production Manager OWN 60000.0 Late (16-30 days) null 1000.0 36 months 11.49 B MD Senior Research Manager RENT 95000.0 Fully Paid null 1000.0 36 months 11.99 C FL Adjunct faculty RENT 26000.0 Fully Paid null 1000.0 36 months 11.99 C IL optical tachnician RENT 40000.0 Fully Paid null 1000.0 36 months 12.29 C OH District Manager MORTGAGE 41600.0 Fully Paid null 1000.0 36 months 12.49 B TX Assistant Principal RENT 61000.0 Fully Paid null 1000.0 36 months 12.62 C NY Sales associate RENT 12000.0 Current null 1000.0 36 months 12.74 C TN Site Support Technician OWN 38400.0 Current null 1000.0 36 months 12.74 C KY team member RENT 40000.0 Current null 1000.0 36 months 12.79 C TX Night manager RENT 22000.0 Current null 1000.0 36 months 12.99 C MD INSIDE SALES REP RENT 53000.0 Current null 1000.0 36 months 12.99 C NY case manager/counselor RENT 35000.0 Fully Paid null 1000.0 36 months 12.99 C PA Recruiting & Sale

-sandbox
<div style="float:left; padding-right:10px; margin-top:20px;">
  <img src='https://jixjiadatabricks.blob.core.windows.net/images/data-lake-no-label.png' width='70px'>
</div>
<div style="float:left;">
  <h3>タイムトラベルで過去へ戻ろうく</h3>
  Delta Lakeのログを利用して<span style="color:green"><strong>以前のデータスナップショット</strong></span>を取得したり、<br>データ<span style="color:green"><strong>変更履歴の監査</strong></span>をしたり、<span style="color:green"><strong>ロールバック</strong></span>をすることが容易に出来ます
</div>

In [0]:
%sql
-- Describe History機能でデータの変更履歴を監査
Describe History LBS

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata 3 2021-12-08T13:05:16.000+0000 102428 masahiko.kitamura@databricks.com WRITE Map(mode -> Append, partitionBy -> []) null List(10034168) 0804-214524-boded127 2 WriteSerializable false Map(numFiles -> 1, numOutputBytes -> 3146, numOutputRows -> 10) null 2 2021-12-08T13:05:03.000+0000 102428 masahiko.kitamura@databricks.com MERGE Map(predicate -> (target.`State` = source.`State`), matchedPredicates -> [{"actionType":"update"}], notMatchedPredicates -> [{"actionType":"insert"}]) null List(10034168) 0804-214524-boded127 1 WriteSerializable false Map(numTargetRowsCopied -> 0, numTargetRowsDeleted -> 0, numTargetFilesAdded -> 1, executionTimeMs -> 1488, numTargetRowsInserted -> 1, scanTimeMs -> 914, numTargetRowsUpdated -> 0, numOutputRows -> 1, numTargetChangeFilesAdded -> 0, numSourceRows -> 1, numTargetFilesRemoved -> 0, rewriteTimeMs -> 514) null 1 2021-12-08T13:04:40.000+0000 102428 masahiko.kitamura@databricks.com DELETE Map(predicate -> ["(spark_catalog.delta_db_masahiko_kitamura_databricks_com.LBS.`State` = 'WA')"]) null List(10034168) 0804-214524-boded127 0 WriteSerializable false Map(numRemovedFiles -> 4, numCopiedRows -> 72652, numAddedChangeFiles -> 0, executionTimeMs -> 1111, numDeletedRows -> 1616, scanTimeMs -> 397, numAddedFiles -> 4, rewriteTimeMs -> 713) null 0 2021-12-08T13:04:31.000+0000 102428 masahiko.kitamura@databricks.com WRITE Map(mode -> Overwrite, partitionBy -> []) null List(10034168) 0804-214524-boded127 null WriteSerializable false Map(numFiles -> 4, numOutputBytes -> 1007927, numOutputRows -> 74268) null

In [0]:
%sql
-- バージョンを指定してスナップショットを取得
Select * 
From LBS Version AS OF 2

loan_amnt term int_rate grade state emp_title home_ownership annual_inc loan_status 1000.0 36 months 5.32 A NY Transit Property Protection Supervisor RENT 62500.0 Current 1000.0 36 months 6.49 A OH Customers Service Consultant RENT 40000.0 Current 1000.0 36 months 6.49 A NY dental assistant RENT 28000.0 Current 1000.0 36 months 6.99 A TN Manager OWN 100000.0 Fully Paid 1000.0 36 months 7.24 A CA Administrative assistant MORTGAGE 48000.0 Current 1000.0 36 months 7.24 A IL Busser/Expo OWN 12000.0 Current 1000.0 36 months 7.49 A CO Teacher MORTGAGE 90000.0 Current 1000.0 36 months 8.18 B CO Admin Officer MORTGAGE 87000.0 Current 1000.0 36 months 8.24 B NY Regional Account Manager OWN 72000.0 Current 1000.0 36 months 8.24 B VA Sales,delivery RENT 44000.0 Current 1000.0 36 months 8.38 B VA Attorney MORTGAGE 110000.0 Current 1000.0 36 months 8.39 B MD Computer Technician MORTGAGE 46500.0 Fully Paid 1000.0 36 months 8.49 B NJ Sales RENT 100000.0 Current 1000.0 36 months 9.17 B VA Inside sales RENT 45000.0 Fully Paid 1000.0 36 months 9.75 B CA Police officer MORTGAGE 90000.0 Fully Paid 1000.0 36 months 9.76 B UT null MORTGAGE 37000.0 Fully Paid 1000.0 36 months 9.76 B NY Exec. Asst. OWN 74000.0 Fully Paid 1000.0 36 months 9.99 B VA Transplant Immunology Technologist MORTGAGE 50000.0 Fully Paid 1000.0 36 months 9.99 B NC registered nurse MORTGAGE 64000.0 Fully Paid 1000.0 36 months 10.49 B SC office manager MORTGAGE 36000.0 Current 1000.0 36 months 10.49 B AR Manager OWN 17000.0 Fully Paid 1000.0 36 months 10.64 B CA School Psychologist OWN 100380.0 Charged Off 1000.0 36 months 10.78 B KS Intensive supervision officer RENT 27000.0 Current 1000.0 36 months 10.78 B LA Registered nurse OWN 62000.0 Current 1000.0 36 months 10.99 B TX Claims Adjuster RENT 50000.0 Fully Paid 1000.0 36 months 10.99 B TX Sales Manager RENT 50000.0 Fully Paid 1000.0 36 months 11.22 B FL null RENT 30000.0 Current 1000.0 36 months 11.39 B NY Director of Operations RENT 70000.0 Current 1000.0 36 months 11.39 B CA Teacher MORTGAGE 75000.0 Current 1000.0 36 months 11.44 B IN Driver MORTGAGE 69000.0 Fully Paid 1000.0 36 months 11.44 B PA Food Service Instructor MORTGAGE 60000.0 Fully Paid 1000.0 36 months 11.44 B SC Picker RENT 25000.0 Fully Paid 1000.0 36 months 11.44 B FL Shipper OWN 32000.0 Current 1000.0 36 months 11.44 B NC project coordinator RENT 42000.0 Current 1000.0 36 months 11.47 B CA Legal Secretary OWN 31000.0 Fully Paid 1000.0 36 months 11.48 B AZ Public Safety Supervisor RENT 95000.0 Fully Paid 1000.0 36 months 11.48 B TX SALVAGE INVENTORY SPECIALIST RENT 48000.0 Current 1000.0 36 months 11.49 B IN null RENT 7700.0 Fully Paid 1000.0 36 months 11.49 B CA null RENT 64800.0 Current 1000.0 36 months 11.49 B MS Administrative Assistant MORTGAGE 32000.0 Current 1000.0 36 months 11.49 B CA CSR RENT 36969.0 Fully Paid 1000.0 36 months 11.49 B AZ Production Manager OWN 60000.0 Late (16-30 days) 1000.0 36 months 11.49 B MD Senior Research Manager RENT 95000.0 Fully Paid 1000.0 36 months 11.99 C FL Adjunct faculty RENT 26000.0 Fully Paid 1000.0 36 months 11.99 C IL optical tachnician RENT 40000.0 Fully Paid 1000.0 36 months 12.29 C OH District Manager MORTGAGE 41600.0 Fully Paid 1000.0 36 months 12.49 B TX Assistant Principal RENT 61000.0 Fully Paid 1000.0 36 months 12.62 C NY Sales associate RENT 12000.0 Current 1000.0 36 months 12.74 C TN Site Support Technician OWN 38400.0 Current 1000.0 36 months 12.74 C KY team member RENT 40000.0 Current 1000.0 36 months 12.79 C TX Night manager RENT 22000.0 Current 1000.0 36 months 12.99 C MD INSIDE SALES REP RENT 53000.0 Current 1000.0 36 months 12.99 C NY case manager/counselor RENT 35000.0 Fully Paid 1000.0 36 months 12.99 C PA Recruiting & Sales Delivery Manager MORTGAGE 94000.0 Current 1000.0 36 months 13.18 C OH Payroll Administrator RENT 35360.0 Current 1000.0 36 months 13.18 C NJ Payroll Coordinator RENT 62000.0 Fully Paid 1000.0 36 months 13.18 C CO senior material handler MORTGAGE 38000.0 Fully Paid 1000.0 36 mo

In [0]:
# 時間をしてしてスナップショットを取得
desiredTimestamp = spark.sql("Select timestamp From (Describe History LBS) Order By timestamp Desc").take(10)[-1].timestamp

print(f'desiredTimestamp => {desiredTimestamp}')

display(
  sql(f"Select * From LBS TIMESTAMP AS OF '{desiredTimestamp}'")
)

desiredTimestamp => 2021-12-08 13:04:31

loan_amnt term int_rate grade state emp_title home_ownership annual_inc loan_status 1000.0 36 months 5.32 A NY Transit Property Protection Supervisor RENT 62500.0 Current 1000.0 36 months 6.49 A OH Customers Service Consultant RENT 40000.0 Current 1000.0 36 months 6.49 A NY dental assistant RENT 28000.0 Current 1000.0 36 months 6.99 A TN Manager OWN 100000.0 Fully Paid 1000.0 36 months 7.24 A CA Administrative assistant MORTGAGE 48000.0 Current 1000.0 36 months 7.24 A IL Busser/Expo OWN 12000.0 Current 1000.0 36 months 7.49 A CO Teacher MORTGAGE 90000.0 Current 1000.0 36 months 7.97 A WA Medical billet RENT 48000.0 Current 1000.0 36 months 8.18 B CO Admin Officer MORTGAGE 87000.0 Current 1000.0 36 months 8.24 B NY Regional Account Manager OWN 72000.0 Current 1000.0 36 months 8.24 B VA Sales,delivery RENT 44000.0 Current 1000.0 36 months 8.38 B VA Attorney MORTGAGE 110000.0 Current 1000.0 36 months 8.39 B MD Computer Technician MORTGAGE 46500.0 Fully Paid 1000.0 36 months 8.49 B NJ Sales RENT 100000.0 Current 1000.0 36 months 9.17 B VA Inside sales RENT 45000.0 Fully Paid 1000.0 36 months 9.75 B CA Police officer MORTGAGE 90000.0 Fully Paid 1000.0 36 months 9.76 B UT null MORTGAGE 37000.0 Fully Paid 1000.0 36 months 9.76 B NY Exec. Asst. OWN 74000.0 Fully Paid 1000.0 36 months 9.99 B VA Transplant Immunology Technologist MORTGAGE 50000.0 Fully Paid 1000.0 36 months 9.99 B NC registered nurse MORTGAGE 64000.0 Fully Paid 1000.0 36 months 10.49 B SC office manager MORTGAGE 36000.0 Current 1000.0 36 months 10.49 B WA sales RENT 40000.0 Current 1000.0 36 months 10.49 B WA Associate Professor RENT 64000.0 Fully Paid 1000.0 36 months 10.49 B AR Manager OWN 17000.0 Fully Paid 1000.0 36 months 10.64 B CA School Psychologist OWN 100380.0 Charged Off 1000.0 36 months 10.78 B KS Intensive supervision officer RENT 27000.0 Current 1000.0 36 months 10.78 B LA Registered nurse OWN 62000.0 Current 1000.0 36 months 10.99 B TX Claims Adjuster RENT 50000.0 Fully Paid 1000.0 36 months 10.99 B TX Sales Manager RENT 50000.0 Fully Paid 1000.0 36 months 11.22 B FL null RENT 30000.0 Current 1000.0 36 months 11.39 B NY Director of Operations RENT 70000.0 Current 1000.0 36 months 11.39 B CA Teacher MORTGAGE 75000.0 Current 1000.0 36 months 11.44 B IN Driver MORTGAGE 69000.0 Fully Paid 1000.0 36 months 11.44 B PA Food Service Instructor MORTGAGE 60000.0 Fully Paid 1000.0 36 months 11.44 B SC Picker RENT 25000.0 Fully Paid 1000.0 36 months 11.44 B FL Shipper OWN 32000.0 Current 1000.0 36 months 11.44 B NC project coordinator RENT 42000.0 Current 1000.0 36 months 11.47 B CA Legal Secretary OWN 31000.0 Fully Paid 1000.0 36 months 11.48 B AZ Public Safety Supervisor RENT 95000.0 Fully Paid 1000.0 36 months 11.48 B TX SALVAGE INVENTORY SPECIALIST RENT 48000.0 Current 1000.0 36 months 11.49 B IN null RENT 7700.0 Fully Paid 1000.0 36 months 11.49 B CA null RENT 64800.0 Current 1000.0 36 months 11.49 B MS Administrative Assistant MORTGAGE 32000.0 Current 1000.0 36 months 11.49 B CA CSR RENT 36969.0 Fully Paid 1000.0 36 months 11.49 B AZ Production Manager OWN 60000.0 Late (16-30 days) 1000.0 36 months 11.49 B MD Senior Research Manager RENT 95000.0 Fully Paid 1000.0 36 months 11.99 C FL Adjunct faculty RENT 26000.0 Fully Paid 1000.0 36 months 11.99 C IL optical tachnician RENT 40000.0 Fully Paid 1000.0 36 months 12.29 C OH District Manager MORTGAGE 41600.0 Fully Paid 1000.0 36 months 12.49 B TX Assistant Principal RENT 61000.0 Fully Paid 1000.0 36 months 12.62 C NY Sales associate RENT 12000.0 Current 1000.0 36 months 12.74 C TN Site Support Technician OWN 38400.0 Current 1000.0 36 months 12.74 C KY team member RENT 40000.0 Current 1000.0 36 months 12.79 C TX Night manager RENT 22000.0 Current 1000.0 36 months 12.99 C MD INSIDE SALES REP RENT 53000.0 Current 1000.0 36 months 12.99 C NY case manager/counselor RENT 35000.0 Fully Paid 1000.0 36 months 12.99 C PA Recruiting & Sales Delivery Manager MORTGAGE 94000.0 Current 1000.0 36 months 13.18 C OH Payroll Administr

-sandbox
<div style="float:left; padding-right:10px; margin-top:20px;">
  <img src='https://jixjiadatabricks.blob.core.windows.net/images/data-lake-no-label.png' width='70px'>
</div>
<div style="float:left;">
  <h3>OPTIMIZEで性能を向上させるく</h3>
  小さなファイルを合併してくれる<span style="color:green"><strong>Optimize</strong></span>コマンドをはじめ<br>、<span style="color:green"><strong>Data Skpping</strong></span>,<span style="color:green"><strong>ZOrder Clustering</strong></span>などの機能をを利用して、<br>クエリ検索性能の向上を容易に実現します。
</div>

In [0]:
%sql
-- OPTIMIZEでデータをコンパクト化、インデックス作成。更にZORDERで良く使われるカラムのデータを物理的に一カ所へまとめる
OPTIMIZE LBS ZORDER By (state)

In [0]:
%sql
-- セル10と全く同じクエリを実行
Select state, loan_status, count(*) as counts 
From LBS
Group by state, loan_status
Order by counts desc

-sandbox 
<div style="float:left; padding-right:10px; margin-top:20px;">
  <img src='https://jixjiadatabricks.blob.core.windows.net/images/data-lake-no-label.png' width='70px'>
</div>
<div style="float:left;">
  <h3>BatchとStreamingの統合</h3>
  Delta Lake/SparkはStraeming処理をバッチ処理と同等に扱えます。ここでは、WikipediaのIRCチャットの内容を受信しているKafkaサーバからリアルタイムでデータを読み込むサンプルを見ていきましょう。
  
  <img src="https://jixjiadatabricks.blob.core.windows.net/images/delta_architecture_demo.gif" width="1200px">

   <h4>Kafkaサーバー情報</h4>
  <table>
    <tr><td>オプション名</td><td>kafka.bootstrap.servers</td></tr>
    <tr><td>サーバー名</td><td>server2.databricks.training:9092</td></tr>
    <tr><td>トピック</td><td>en</td></tr>
  </table>
  <br>
  <h4>JSONストリーム</h4>
  <p>DatabricksではWikipediaの公式IRCチャネルから編集データを受信し、JSONに変換して自社Kafkaサーバーへ送信しています。
    <br>今回はこのKafkaサーバーに流れ込んだ英語の記事(トピック)にサブスクライブし、リアルタイムで処理していきます。

In [0]:
from pyspark.sql.types import *
from pyspark.sql.functions import from_json, col
import re

# ファイルパスの設定(書き込み先など)
## Username を取得。
username_raw = dbutils.notebook.entry_point.getDbutils().notebook().getContext().tags().apply('user')
## Username の英数字以外を除去し、全て小文字化。Usernameをファイルパスやデータベース名の一部で使用可能にするため。
username = re.sub('[^A-Za-z0-9]+', '_', username_raw).lower()

homeDir = f'/home/{username}/streaming/wikipedia/'
bronzePath = homeDir + "bronze.delta"
bronzeCkpt = homeDir + "bronze.checkpoint"

# 保存先をリセット
dbutils.fs.rm(homeDir, True)

#　JSONデータのスキーマ定義
schema = StructType([
  StructField("channel", StringType(), True),
  StructField("comment", StringType(), True),
  StructField("delta", IntegerType(), True),
  StructField("flag", StringType(), True),
  StructField("geocoding", StructType([
    StructField("city", StringType(), True),
    StructField("country", StringType(), True),
    StructField("countryCode2", StringType(), True),
    StructField("countryCode3", StringType(), True),
    StructField("stateProvince", StringType(), True),
    StructField("latitude", DoubleType(), True),
    StructField("longitude", DoubleType(), True),
  ]), True),
  StructField("isAnonymous", BooleanType(), True),
  StructField("isNewPage", BooleanType(), True),
  StructField("isRobot", BooleanType(), True),
  StructField("isUnpatrolled", BooleanType(), True),
  StructField("namespace", StringType(), True),         
  StructField("page", StringType(), True),              
  StructField("pageURL", StringType(), True),           
  StructField("timestamp", StringType(), True),        
  StructField("url", StringType(), True),
  StructField("user", StringType(), True),              
  StructField("userURL", StringType(), True),
  StructField("wikipediaURL", StringType(), True),
  StructField("wikipedia", StringType(), True),
])

#　JSONストリームを解析し、Deltaに保存
input_DF = (
  spark
  .readStream
  .format('kafka')                          # Kafkaをソースと指定
  .option('kafka.bootstrap.servers', 
          'server2.databricks.training:9092')
  .option('subscribe', 'en')
  .load()
)

# ELTをして、Deltaに書き込む
(
  input_DF
  .withColumn('json', from_json(col('value').cast('string'), schema))   # Kafkaのバイナリデータを文字列に変換し、from_json()でJSONをパース
  .select(col("json.*"))                    # JSONの子要素だけを取り出す
  .writeStream                              # writeStream()でストリームを書き出す
  .format('delta')                          # Deltaとして保存
  .option('checkpointLocation', bronzeCkpt) # チェックポイント保存先を指定
  .outputMode('append')                     # マイクロバッチの結果をAppendで追加
  .queryName('Bronze Stream')               # ストリームに名前を付ける（推奨）
  .start(bronzePath)                        # start()でストリーム処理を開始 (アクション)
)

### 以下の2つのコードの違いはどこにありますか?

In [0]:
# データフレームの確認
df = spark.read.format('delta').load(bronzePath)

display( df )

In [0]:
# データフレームの確認2
df = spark.readStream.format('delta').load(bronzePath)

display( df )

### StreamingはSQLからも参照可能です

In [0]:
spark.readStream.format('delta').load(bronzePath).createOrReplaceTempView('tmp_wikipedia_msg')

In [0]:
%sql
SELECT geocoding.countryCode3, count(*) FROM tmp_wikipedia_msg
WHERE geocoding.countryCode3 is not null
GROUP BY geocoding.countryCode3
ORDER BY geocoding.countryCode3

## END
&copy; 2021 Copyright by Jixin Jia (Gin), Masahiko Kitamura
<hr>

In [0]:
sql(f'DROP DATABASE {dbname} CASCADE')
dbutils.fs.rm(delta_path, True)
dbutils.fs.rm(homeDir, True)
dbutils.fs.rm(f'/tmp/{username}', True)


